In [1]:
import numpy as np
import pandas as pd
import glob
import os
import matplotlib.pyplot as plt
from tqdm.notebook import tqdm
from pathlib import Path
import multiprocessing
from scipy.spatial.distance import cdist
import yaml
from datetime import datetime

import warnings
warnings.simplefilter('ignore')

In [2]:
def init_logger(log_file='logger.log'):
    from logging import getLogger, INFO, FileHandler,  Formatter,  StreamHandler
    logger = getLogger(__name__)
    logger.setLevel(INFO)
    handler1 = StreamHandler()
    handler1.setFormatter(Formatter("%(message)s"))
    handler2 = FileHandler(filename=log_file)
    handler2.setFormatter(Formatter("%(message)s"))
    logger.addHandler(handler1)
    logger.addHandler(handler2)
    return logger
    
today = datetime.now().strftime('%Y-%m-%d')
logger = init_logger(log_file=f'./{today}.log')
logger.info('Start Logging...')

Start Logging...


In [3]:
def seed_everything(seed: int):
    random.seed(seed)
    os.environ["PYTHONHASHSEED"] = str(seed)
    np.random.seed(seed)

In [4]:
import pickle
def to_pickle(filename, obj):
    with open(filename, mode='wb') as f:
        pickle.dump(obj, f)
        
def from_pickle(filename):
    with open(filename, mode='rb') as f:
        obj = pickle.load(f)
    return obj

In [5]:
# config
with open('config.yaml') as f:
    config = yaml.safe_load(f)

# globals variable
SEED = config['globals']['seed']
N_SPLITS = config['globals']['n_splits']
USE_FOLDS = config['globals']['use_folds']
DEBUG = config['globals']['debug']
EXP_MESSAGE = config['globals']['exp_message']
NOTES = config['globals']['notes']
EXP_NAME = str(Path().resolve()).split('/')[-1]

# waypointを補正したdataset
root_dir = Path('../../input')
data_dir = root_dir/'google-smartphone-decimeter-challenge'
collection_type_dict = from_pickle(root_dir/"road_type.pkl") # by edge'sdegree and highway feature

In [6]:
import plotly.express as px

def visualize_trafic(df):
    fig = px.scatter_mapbox(df,
                            
                            # Here, plotly gets, (x,y) coordinates
                            lat="latDeg",
                            lon="lngDeg",
                            text='phoneName',
                            
                            #Here, plotly detects color of series
                            color="collectionName",
                            labels="collectionName",
                            
                            zoom=9,
                            center={"lat":37.423576, "lon":-122.094132},
                            height=600,
                            width=800)
    fig.update_layout(mapbox_style='stamen-terrain')
    fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
    fig.update_layout(title_text="GPS trafic")
    fig.show()


def visualize_collection(df, hover_data=["elapsed_epoch", "speedMps"], collection_name='2021-04-29-US-SJC-2'):
    gt_df = pd.read_csv(root_dir / 'all_ground_truth.csv')
    gt_df['phoneName'] = 'ground truth'
    gt_df = pd.concat([df, gt_df])
    target_df = gt_df[gt_df['collectionName']==collection_name]   
    target_df['elapsed_epoch'] = ((target_df['millisSinceGpsEpoch'] - target_df['millisSinceGpsEpoch'].min()) / 1000)
    fig = px.scatter_mapbox(target_df,
                                
                            # Here, plotly gets, (x,y) coordinates
                            lat="latDeg",
                            lon="lngDeg",
                                
                            #Here, plotly detects color of series
                            color="phoneName",
                            labels="phoneName",
                            hover_data=hover_data,                

                                
                            zoom=9,
                            center={"lat":37.423576, "lon":-122.094132},
                            height=600,
                            width=800)
    fig.update_layout(mapbox_style='stamen-terrain')
    fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
    fig.update_layout(title_text="{collection_name}")
    fig.show()

In [7]:
# metric
def calc_haversine(lat1, lon1, lat2, lon2):
    """Calculates the great circle distance between two points
    on the earth. Inputs are array-like and specified in decimal degrees.
    """
    RADIUS = 6_367_000
    lat1, lon1, lat2, lon2 = map(np.radians, [lat1, lon1, lat2, lon2])
    dlat = lat2 - lat1
    dlon = lon2 - lon1
    a = np.sin(dlat/2)**2 + \
        np.cos(lat1) * np.cos(lat2) * np.sin(dlon/2)**2
    dist = 2 * RADIUS * np.arcsin(a**0.5)
    return dist

def check_score(input_df: pd.DataFrame) -> pd.DataFrame:
    if "phone" not in input_df.columns:
        input_df["phone"] = input_df["collectionName"] + "_" + input_df["phoneName"]

    if "target_latDeg" not in input_df.columns:
        processes = multiprocessing.cpu_count()
        with multiprocessing.Pool(processes=processes) as pool:
            gr = input_df.groupby(['collectionName','phoneName'])
            dfs = pool.imap_unordered(get_ground_truth, gr)
            dfs = tqdm(dfs, total=len(gr))
            dfs = list(dfs)
        input_df = pd.concat(dfs).sort_values(['collectionName', 'phoneName', 'millisSinceGpsEpoch']).reset_index(drop=True)     


    output_df = input_df.copy()
    
    output_df['error'] = input_df.apply(
        lambda r: calc_haversine(
            r.latDeg, r.lngDeg, r.target_latDeg, r.target_lngDeg
        ),
        axis=1
    )

    meter_score = output_df['error'].mean()
    logger.info(f'mean error: {meter_score}')

    scores = []
    p_50_scores = []
    p_95_scores = []
    mean_scores = []
    phones = []
    score_df = pd.DataFrame()
    for phone in output_df['phone'].unique():
        _index = output_df['phone']==phone
        p_50 = np.percentile(output_df.loc[_index, 'error'], 50)
        p_95 = np.percentile(output_df.loc[_index, 'error'], 95)
        # print(f"{phone} | 50:{p_50:.5g}| 95:{p_95:.5g}")
        p_50_scores.append(p_50)
        p_95_scores.append(p_95)
        mean_scores.append(np.mean([p_50, p_95]))
        phones.append(phone)

        scores.append(p_50)
        scores.append(p_95)

    score_df["phone"] = phones
    score_df["p_50_score"] = p_50_scores
    score_df["p_95_score"] = p_95_scores
    score_df["mean_score"] = mean_scores
    
    comp_score = sum(scores) / len(scores)
    logger.info(f"competition metric:{comp_score}")
    return output_df, score_df

## test

In [21]:
sub_df = pd.read_csv(f'../exp038/exp038_submission.csv')

In [22]:
sub_df['collectionName'] = sub_df['phone'].str.split('_', expand=True)[0]
sub_df

phone  millisSinceGpsEpoch     latDeg  \
0               2020-05-15-US-MTV-1_Pixel4        1273608785432  37.416560   
1               2020-05-15-US-MTV-1_Pixel4        1273608786432  37.416560   
2               2020-05-15-US-MTV-1_Pixel4        1273608787432  37.416560   
3               2020-05-15-US-MTV-1_Pixel4        1273608788432  37.416560   
4               2020-05-15-US-MTV-1_Pixel4        1273608789432  37.416560   
...                                    ...                  ...        ...   
91481  2021-04-29-US-SJC-3_SamsungS20Ultra        1303763185000  37.334592   
91482  2021-04-29-US-SJC-3_SamsungS20Ultra        1303763186000  37.334592   
91483  2021-04-29-US-SJC-3_SamsungS20Ultra        1303763187000  37.334592   
91484  2021-04-29-US-SJC-3_SamsungS20Ultra        1303763188000  37.334592   
91485  2021-04-29-US-SJC-3_SamsungS20Ultra        1303763189000  37.334592   

           lngDeg       collectionName  
0     -122.082075  2020-05-15-US-MTV-1  
1     -122.082075  2020-05-15-US-MTV-1  
2     -122.082075  2020-05-15-US-MTV-1  
3     -122.082075  2020-05-15-US-MTV-1  
4     -122.082075  2020-05-15-US-MTV-1  
...           ...                  ...  
91481 -121.899417  2021-04-29-US-SJC-3  
91482 -121.899417  2021-04-29-US-SJC-3  
91483 -121.899417  2021-04-29-US-SJC-3  
91484 -121.899417  2021-04-29-US-SJC-3  
91485 -121.899417  2021-04-29-US-SJC-3  

[91486 rows x 5 columns]

In [ ]:
/len(sub_df)

In [23]:
target_collection = [
"2020-05-15-US-MTV-1",
"2020-05-28-US-MTV-1",
"2020-06-04-US-MTV-2",
"2020-08-03-US-MTV-2",
"2021-03-16-US-RWC-2",
"2021-03-25-US-PAO-1",
"2021-04-08-US-MTV-1",
"2021-04-22-US-SJC-2",
]
len(sub_df.loc[sub_df['collectionName'].isin(target_collection)])/len(sub_df)

0.4720285070939816

In [24]:
len(sub_df.loc[sub_df['collectionName'].isin(target_collection)])

43184

In [18]:

fig = px.scatter_mapbox(sub_df,                              
                        # Here, plotly gets, (x,y) coordinates
                        lat="latDeg",
                        lon="lngDeg",
                            
                        #Here, plotly detects color of series
                        color="collectionName",
                        labels="collectionName",
                            
                        zoom=9,
                        center={"lat":37.423576, "lon":-122.094132},
                        height=600,
                        width=800)
fig.update_layout(mapbox_style='stamen-terrain')
fig.update_layout(margin={"r": 0, "t": 0, "l": 0, "b": 0})
# fig.update_layout(title_text="{collection_name}")
fig.show()


In [20]:
# sub_df[['phone','millisSinceGpsEpoch','latDeg','lngDeg']].to_csv(f'{target_collection}.csv', index=False)
sub_df[['phone','millisSinceGpsEpoch','latDeg','lngDeg']].to_csv(f'private.csv', index=False)